In [1]:
import cv2
import numpy as np
import os
import math
from random import shuffle
from tqdm import tqdm
import tensorflow as tf
import matplotlib.pyplot as plt
%matplotlib inline



train_data = 'train'
test_data  = 'test'


def one_hot_label(img):
    label = img.split('_')[0]
    if label == 'c':
        ohl = np.array([1,0])
    elif label == 'nc':
        ohl = np.array([0,1])
    return ohl


def train_data_with_label():
    train_images = []
    for i in tqdm(os.listdir(train_data)):
        path = os.path.join(train_data, i)
        
        img = cv2.imread(path)

        '''TARGET_PIXEL_AREA = 100000.0

        ratio = float(img.shape[1]) / float(img.shape[0])
        new_h = int(math.sqrt(TARGET_PIXEL_AREA / ratio) + 0.5)
        new_w = int((new_h * ratio) + 0.5)

        img = cv2.resize(img, (new_w,new_h))'''
        img = cv2.imread(path, cv2.IMREAD_COLOR)
        '''img = cv2.imread(path, cv2.IMREAD_UNCHANGED)
        scale_percent = 60 # percent of original size
        width = int(img.shape[1] * scale_percent / 100)
        height = int(img.shape[0] * scale_percent / 100)
        dim = (width, height)
        img = cv2.resize(img, dim, interpolation = cv2.INTER_AREA)'''
        #img = cv2.imread(path, cv2.IMREAD_GRAYSCALE)
        img = cv2.resize(img, (200,200))
        train_images.append([np.array(img), one_hot_label(i)])
    shuffle(train_images)
    return train_images


def test_data_with_label():
    test_images = []
    for i in tqdm(os.listdir(test_data)):
        path = os.path.join(test_data, i)
        img = cv2.imread(path)

        img = cv2.imread(path, cv2.IMREAD_COLOR)
        #img = cv2.imread(path, cv2.IMREAD_GRAYSCALE)
        img = cv2.resize(img, (200,200))
        
        '''img = cv2.imread(path, cv2.IMREAD_GRAYSCALE)
        scale_percent = 80 # percent of original size
        width = int(img.shape[1] * scale_percent / 100)
        height = int(img.shape[0] * scale_percent / 100)
        dim = (width, height)
        img = cv2.resize(img, dim, interpolation = cv2.INTER_AREA)'''
        #img = cv2.imread(path, cv2.IMREAD_GRAYSCALE)
        #img = cv2.resize(img, (64,64))
        
        '''TARGET_PIXEL_AREA = 100000.0

        ratio = float(img.shape[1]) / float(img.shape[0])
        new_h = int(math.sqrt(TARGET_PIXEL_AREA / ratio) + 0.5)
        new_w = int((new_h * ratio) + 0.5)

        img = cv2.resize(img, (new_w,new_h))'''

        test_images.append([np.array(img), one_hot_label(i)])
    return test_images


/home/ubuntu/.local/lib/python3.7/site-packages/tensorflow/python/framework/dtypes.py:516: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint8 = np.dtype([("qint8", np.int8, 1)])
/home/ubuntu/.local/lib/python3.7/site-packages/tensorflow/python/framework/dtypes.py:517: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_quint8 = np.dtype([("quint8", np.uint8, 1)])
/home/ubuntu/.local/lib/python3.7/site-packages/tensorflow/python/framework/dtypes.py:518: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint16 = np.dtype([("qint16", np.int16, 1)])
/home/ubuntu/.local/lib/python3.7/site-packages/tensorflow/python/framework/dtypes.py:519: 

In [2]:
from tensorflow import keras
from keras.models import Sequential
from keras.layers import *
from keras.optimizers import *


training_images = train_data_with_label()
testing_images = test_data_with_label()
tr_img_data = np.array([i[0] for i in training_images]).reshape(-1,200,200,3)
tr_lbl_data = np.array([i[1] for i in training_images])
tst_img_data = np.array([i[0] for i in testing_images]).reshape(-1,200,200,3)
tst_lbl_data = np.array([i[1] for i in testing_images])



model = Sequential()

model.add(InputLayer(input_shape=[200,200, 3]))
model.add(Conv2D(filters=32,kernel_size=5,strides=1,padding='same', activation='relu'))
model.add(MaxPool2D(pool_size=5,padding='same'))

model.add(Conv2D(filters=50,kernel_size=5,strides=1,padding='same', activation='relu'))
model.add(MaxPool2D(pool_size=5,padding='same'))

model.add(Conv2D(filters=50,kernel_size=5,strides=1,padding='same', activation='relu'))
model.add(MaxPool2D(pool_size=5,padding='same'))

model.add(Conv2D(filters=50,kernel_size=5,strides=1,padding='same', activation='relu'))
model.add(MaxPool2D(pool_size=5,padding='same'))

model.add(Conv2D(filters=50,kernel_size=5,strides=1,padding='same', activation='relu'))
model.add(MaxPool2D(pool_size=5,padding='same'))


model.add(Conv2D(filters=50,kernel_size=5,strides=1,padding='same', activation='relu'))
model.add(MaxPool2D(pool_size=5,padding='same'))

model.add(Conv2D(filters=50,kernel_size=5,strides=1,padding='same', activation='relu'))
model.add(MaxPool2D(pool_size=5,padding='same'))


model.add(Conv2D(filters=80,kernel_size=5,strides=1,padding='same', activation='relu'))
model.add(MaxPool2D(pool_size=5,padding='same'))

model.add(Dropout(0.25))
model.add(Flatten())
model.add(Dense(512,activation='relu'))
model.add(Dropout(rate=0.5))
model.add(Dense(2,activation='softmax'))
optimizer = Adam(lr=1e-3)

model.compile(optimizer=optimizer,loss='categorical_crossentropy',metrics=['accuracy'])
model.fit(x=tr_img_data,y=tr_lbl_data,epochs=50,batch_size=150)
model.summary()

Using TensorFlow backend.
100%|██████████| 76/76 [00:01<00:00, 62.47it/s]
W0820 00:29:13.828004 139701792089920 deprecation_wrapper.py:119] From /usr/local/lib/python3.7/dist-packages/keras/backend/tensorflow_backend.py:74: The name tf.get_default_graph is deprecated. Please use tf.compat.v1.get_default_graph instead.

W0820 00:29:13.911465 139701792089920 deprecation_wrapper.py:119] From /usr/local/lib/python3.7/dist-packages/keras/backend/tensorflow_backend.py:517: The name tf.placeholder is deprecated. Please use tf.compat.v1.placeholder instead.

W0820 00:29:13.925204 139701792089920 deprecation_wrapper.py:119] From /usr/local/lib/python3.7/dist-packages/keras/backend/tensorflow_backend.py:4138: The name tf.random_uniform is deprecated. Please use tf.random.uniform instead.

W0820 00:29:14.002207 139701792089920 deprecation_wrapper.py:119] From /usr/local/lib/python3.7/dist-packages/keras/backend/tensorflow_backend.py:3976: The name tf.nn.max_pool is deprecated. Please use tf.nn.ma

Epoch 1/50
178/178 [==============================] - 9s 48ms/step - loss: 0.6933 - acc: 0.3708
Epoch 2/50
178/178 [==============================] - 6s 31ms/step - loss: 0.6600 - acc: 0.8427
Epoch 3/50
178/178 [==============================] - 6s 31ms/step - loss: 0.5104 - acc: 0.8427
Epoch 4/50
178/178 [==============================] - 6s 31ms/step - loss: 0.5921 - acc: 0.8427
Epoch 5/50
178/178 [==============================] - 6s 31ms/step - loss: 0.4374 - acc: 0.8427
Epoch 6/50
178/178 [==============================] - 5s 31ms/step - loss: 0.4802 - acc: 0.8427
Epoch 7/50
178/178 [==============================] - 5s 31ms/step - loss: 0.4674 - acc: 0.8427
Epoch 8/50
178/178 [==============================] - 6s 31ms/step - loss: 0.4158 - acc: 0.8427
Epoch 9/50
178/178 [==============================] - 6s 31ms/step - loss: 0.4615 - acc: 0.8427
Epoch 10/50
178/178 [==============================] - 6s 33ms/step - loss: 0.4137 - acc: 0.8427
Epoch 11/50
178/178 [==================

In [20]:
import keras
print(keras.__version__)

2.2.4


In [3]:
fig = plt.figure(figsize=(200,200))
#fig = plt.figure()
#fig=plt.figure(figsize(14, 14))

for cnt, data in enumerate(testing_images[10:40]):
    
    y = fig.add_subplot(6, 5, cnt+1)
    img = data[0]
    data = img.reshape(1,200, 200,3)
    model_out = model.predict([data])
    if np.argmax(model_out) == 1:
        str_label='NonCrack'
    else:
        str_label='Crack'
        
    y.imshow(img)
    #y.imshow(img, cmap='gray')
    plt.title(str_label , fontsize=120,color='royalblue')
    y.axes.get_xaxis().set_visible(False)
    y.axes.get_yaxis().set_visible(False)